# Prediction Explanation clustering with R

This notebook outlines how to use Prediction Explanation clustering with the DataRobot R package, as implemented in the `datarobot.pe.clustering R package`, hosted on the [pe-clustering-R repository](https://github.com/datarobot-community/pe-clustering-R).

Prediction Explanation clustering is a powerful technique used to understand important patterns in the data of a predictive model. It aggregates the row-by-row Prediction Explanations from a DataRobot model to produce clusters of observations with similar profiles of predictive factors for the target of interest.

This notebook explains how to:

* Apply Prediction Explanation methodology to a sample dataset.
* Identify the clusters present in a DataRobot model's Prediction Explanations.
* Characterize and interpret clusters.
* Use Prediction Explanation clusters to inform feature engineering.
* Include Prediction Explanation clusters in an output, consumable alongside model predictions.

### Requirements

In order to use the code provided in this notebook, you must install and configure [the DataRobot R client](https://cran.r-project.org/web/packages/datarobot/index.html).

### Install the clustering package

You can install the `datarobot.pe.clustering` package directly from GitHub. To do so, you need to [set up a GitHub Personal Access (PAT) token](https://help.github.com/articles/creating-a-personal-access-token-for-the-command-line/) and then export `GITHUB_PAT=<token>` into your shell before running `install_github`.

Once set up, run the following commands.

In [3]:
install.packages("mlbench")


The downloaded binary packages are in
	/var/folders/x9/3l8ny90j1g9cx0cx90d3m4440000gr/T//RtmpDaxdJ1/downloaded_packages


In [ ]:
if (!require("remotes")) { install.packages("remotes") }
if (!require("datarobot.pe.clustering")) { remotes::install_github("datarobot-community/pe-clustering-R", build_vignettes=TRUE, upgrade = "never") }

### Import libraries

This notebook uses the `datarobot.pe.clustering` package and a few additional libraries to help illustrate the results.

In [ ]:
library(datarobot.pe.clustering)
library(ggplot2)
library(dplyr)
library(tidyr)
library(mlbench)

### Prepare the data

This notebook uses the "[Pima Indians Diabetes](https://www.kaggle.com/datasets/uciml/pima-indians-diabetes-database)" dataset from the `mlbench` package as a sample dataset. It contains health diagnostic measurements and diabetes diagnoses for 768 women of Pima Indian heritage. To import it, use the following commands.

In [10]:
dataset_file_path <- "/Users/nathan.goudreault/Downloads/diabetes.csv"
training_data <- utils::read.csv(dataset_file_path)
head(training_data)

Pregnancies Glucose BloodPressure SkinThickness Insulin BMI 
1 6           148     72            35              0     33.6
2 1            85     66            29              0     26.6
3 8           183     64             0              0     23.3
4 1            89     66            23             94     28.1
5 0           137     40            35            168     43.1
6 5           116     74             0              0     25.6
  DiabetesPedigreeFunction Age Outcome
1 0.627                    50  1      
2 0.351                    31  0      
3 0.672                    32  1      
4 0.167                    21  0      
5 2.288                    33  1      
6 0.201                    30  0

### Obtain a DataRobot model

Prediction Explanation clustering requires an appropriate DataRobot model. For documentation on fitting models with DataRobot, [reference the `datarobot` package](https://cran.r-project.org/web/packages/datarobot/datarobot.pdf).

For this example, [start a new DataRobot project](https://docs.datarobot.com/en/docs/modeling/build-models/build-basic/model-data.html) with the Pima Indians Diabetes dataset, training models to predict the diabetes diagnosis.

In [ ]:
project <- StartProject(dataSource = training_data,
                        projectName = "PredictionExplanationClusteringVignette",
                        target = "diabetes",
                        mode = "quick",
                        wait = TRUE)
models <- ListModels(project$projectId)
model <- models[[1]]

When modeling completes, this output reports the top-performing model, which will be used in the following steps.

In [ ]:
summary(model)['modelType']

### Run Prediction Explanation clustering

For full validity, run Prediction Explanation clustering on a separate dataset that was not used for training models. However, for example purposes in this notebook, re-use the training dataset.

In [ ]:
scoring_df <- training_data %>% select(-diabetes)

Next, run the Prediction Explanation clustering function. This will run the Prediction Explanations themselves, and then perform the clustering routines on those explanations.

In [ ]:
results <- cluster_and_summarize_prediction_explanations(
      model,
      scoring_df,
      num_feature_summarizations=10,
      num_neighbors=50,
      min_dist=10^-100,
      min_points=25
    )

The results object captures the intermediate and final outputs of the Prediction Explanation clustering process. You can analyze these results in [a variety of ways](#interpret-the-results).

In [ ]:
str(results, max.level = 1)

Sample output:

In [ ]:
List of 5
   plot_data      :'data.frame':	768 obs. of  3 variables:
   summary_data   : tibble [3 × 10] (S3: tbl_df/tbl/data.frame)
   cluster_ids    : num [1:768] 3 2 3 2 3 2 3 2 3 3 ...
   pe_frame       :'data.frame':	768 obs. of  22 variables:
   strength_matrix:'data.frame':	768 obs. of  8 variables:
 - attr(*, "class")= chr "dataRobotPEClusterResults"

When the job completes successfully, you should see the output file in the GCS bucket.

### Interpret the results

You can use `summary()` to view a summary of the clusters based on the features most important to the predictive performance of the model. Notice that the clusters differ on average across a wide array of features:

![](pe-cluster-2.png)

Use `plot()` to plot the results and see how the clusters are distributed in the reduced-dimensionality space. This gives you a sense of how well the clusters are separated from each other in Prediction Explanation space.

![](pe-cluster-3.png)

The same plotting data is available within the results, allowing for plotting through libraries like `ggplot2`:

In [ ]:
ggplot(results$plot_data, aes(x=dim1, y=dim2, color=clusterID)) +
  geom_point()+
  theme_bw()+
  labs(title='Records by Prediction Explanation Cluster', x='Reduced Dimension 1', y='Reduced Dimension 2')

![](pe-cluster-4.png)

### Characterize clusters by prediction risk and feature values

By joining the cluster IDs and predicted scores supplied by the results back to the original dataset, you can get further insight into the patterns captured by the clusters.


In [ ]:
scoring_df_with_clusters <- scoring_df
scoring_df_with_clusters$cluster <- factor(results$cluster_ids)
scoring_df_with_clusters$predicted_risk <- results$pe_frame$class1Probability

For example, you can examine how the predicted risk of diabetes varies by cluster. Here, note that one of the clusters has especially high diabetes risk, while the other two clusters have mostly lower levels of risk.

In [ ]:
scoring_df_with_clusters %>%
    ggplot(aes(x=cluster,y=predicted_risk, fill=cluster))+geom_violin()+
    labs(title='Predicted Diabetes Risk by Cluster')+
    theme_bw()

![](pe-cluster-5.png)

You can also examine how the clusters differ on the original feature values. Based on the distributions of these features, you can see that the clusters differ on a number of different features. Because these clusters are derived from Prediction Explanation clustering, you can have more confidence that the differences between the clusters are associated with meaningful differences in the diabetes risk profile.

In [ ]:
scoring_df_with_clusters %>%
    gather(key='feature',value='value',-cluster)%>%
    ggplot(aes(x=value, group=cluster, color=cluster, fill=cluster)) +
    geom_density(alpha=0.2)+
    facet_wrap(~feature, scales='free')+
    theme_bw()

![](pe-cluster-6.png)

### Characterize clusters by Prediction Explanation strength

In addition to looking at the clusters based on the original features, you can also look at the clusters based on the Prediction Explanation strengths. These will give you insights into which features in the clusters contributed most to the predicted diabetes risk profile of the clusters’ members, and whether a feature’s contribution increased or decreased risk.


In [ ]:
strength_matrix_with_clusters <- results$strength_matrix
strength_matrix_with_clusters$cluster <- factor(results$cluster_ids)
head(strength_matrix_with_clusters)

![](pe-cluster-7.png)

By examining the distribution of Prediction Explanation strengths by cluster, you can see that cluster 1 members tend to have a lower predicted diabetes risk due to their age, glucose levels, and mass. Looking back at the feature values by cluster [above](#characterize-clusters-by-prediction-risk-and-feature-values), cluster 1 tends to be younger, lighter, and have lower glucose levels.

In contrast, cluster 3 members often are predicted to have elevated risks due to age, glucose, and mass. Looking back at the feature values by cluster (above), cluster 3 members tend to be older, heavier, and have higher glucose values.

In [ ]:
strength_matrix_with_clusters %>%
  gather(feature, strength, -cluster)%>%
  ggplot(aes(x=strength, group=cluster, color=cluster, fill=cluster)) +
  geom_density(alpha=0.2)+
  facet_wrap(~feature, scales='free')+
  xlab('Strength of prediction explanation')+
  theme_bw()

![](pe-cluster-8.png)

Using the `datarobot.pe.clustering` R package and the techniques illustrated in this notebook, you can apply this methodology to your own datasets. Download the notebook and adapt it to your own data. Once you are comfortable with how the package works, explore different variations on the methodology coded in the package, and discover what works best for your use case.

## Documentation

* [Python notebook for Prediction Explanation Clustering](https://github.com/datarobot-community/pe-clustering-python)
* [Prediction Explanations](https://docs.datarobot.com/en/docs/modeling/analyze-models/understand/pred-explain/index.html)